# Online Shoppers Purchasing Intention 
### Zoccoli Carlo s267546


#### Index

1. [Introduction](#Introduction) 
2. [Explore the dataset](#Explore-the-Dataset)
    1. [Label Distribution and metric](#Label-Distribution-and-metric)
    2. [Distribution of the features](#Distribution-of-the-features)
    3. [Box plots](#Box-Plots)
    4. [Pie charts](#Pie-Chart)
    5. [Bar charts](#Bar-Chart)

3. [Preparing the dataset](#Preparing-the-dataset)
    1. [Normalization](#Normalization)
    2. [Principal Components Analysis](#Principal-Components-Analysis)
    
4. [Model Classifier](#model)
    1. [K-Neighbors Classifier](#K-Neighbors-Classifier)
    2. [Support Vector Machine](#Support-Vector-Machine)
    3. [Decision Tree Classifier](#DecisionTree-Classifier)
    4. [Random Forest Classifier](#Random-Forest-Classifier)
    
5. [Clustering](#Clustering)
    1. [K-Means](#)
    2. [Hierachical](#Hierarchical)

In [1]:
from IPython.display import HTML

HTML('''<script>
code_show=true; 
function code_toggle() {
 if (code_show){
 $('div.input').hide();
 } else {
 $('div.input').show();
 }
 code_show = !code_show
} 
$( document ).ready(code_toggle);
</script>
<form action="javascript:code_toggle()"><input type="submit" value="Click here to toggle on/off the raw code."></form>''')

### Introduction

The dataset used for this study is the __Online Shoppers Purchasing Intention Dataset__ available at this [link](https://archive.ics.uci.edu/ml/datasets/Online+Shoppers+Purchasing+Intention+Dataset)

The dataset is composed by 12330 sessions, which each session identifies an user, in a period of 1 year to avoid any tendency to a specific compaign, special day, user profile or period. 

The dataset contains 18 attributes, which 10 numerical and 8 categorical attributes.


The attribute are:
* Information about the type of page visited and how much time spent of each categories:
    * *Administrative*
    * *AdministrativeDuration*
    * *Informational* 
    * *InformationalDuration*
    * *ProductRelated*
    * *ProductRelatedDuration*


* Google Analytics's data:
    * *BounceRate*: percentage of visitors who enter the site from that page and then leave ('bounce') without triggering any other requests to the analytics server during that session.
    * *ExitRate*:  is the percentage of people who left your site from that page. Exits may have viewed more than one page in a session. That means they may not have landed on that page, but simply found their way to it through site navigation.
    * *PageValue*: feature represents the average value for a web page that a user visited before completing an e-commerce transaction.
  

* User's navigation data 
    * *OperatingSystem*: type of OS used by the user
    * *Browser*: type of browser used by the user
    * *Region*: user's region of origin 
    * *TrafficType*
    * *VisitorType*: the type of visitor which are: *Returing_Visitator*, *New_Visitator* and *Other*


* Timing attribute:
     * *SpecialDay*: indicate the closeness of the site visiting time to a specific special day in which the the sessions are more likely to tbe finalized with transaction. The value of this attribute is determined by considering the dynamics of e-commerce such as the duration between the order date and delivery date.
     * *Month*

The analysis is done with Python 3.7 and the following packages:
* *Pandas*: it is an open source library that provides data structure and data analysis tool that are very powerful.
* *Numpy*: it is an open source library that provides N-dimensional array objects to allow fast scientific computing.
* *Scikit-learn*: it is an open source machine learning library that supports supervised and unsupervised learning.It provides machine algorithms and also data preprocessing, model selection and evaluation, and many other utilities.
* *Plotly*: it's a graphing library maske interactive, pubblication-quality graphs.
* *ipwidgets*: package that allows to have interactive HTML widgets
* *imbalanced-learn*: package for use under-sampling or over-sampling methods.

In [2]:
import pandas as pd
import numpy as np
import seaborn as sns
import plotly as py
import plotly.graph_objs as go
import plotly.express as px
from plotly import figure_factory as ff
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True) # to show plots in notebook

from matplotlib import pyplot as plt
from matplotlib.colors import ListedColormap
from sklearn.svm import SVC, LinearSVC
from sklearn.pipeline import Pipeline
from sklearn.neighbors import KNeighborsClassifier
from sklearn.model_selection import KFold, GridSearchCV, train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import classification_report, f1_score, silhouette_score, roc_curve, auc
from sklearn.decomposition import PCA
from sklearn.preprocessing import normalize, StandardScaler
from sklearn.cluster import DBSCAN
from sklearn.cluster import KMeans
from sklearn.multiclass import OneVsRestClassifier
from sklearn.cluster import AgglomerativeClustering


from imblearn.over_sampling import SMOTE
from scipy.cluster import hierarchy 

def plotBoundary(X, y, method, costant, title, final = False):
    Z = method.predict(X)
    X = TSNE(n_components=2).fit_transform(X)
    
    cmap_light = ListedColormap(['#FFAAAA', '#AAFFAA', '#AAAAFF'])
    cmap_bold = ListedColormap(['#FF0000', '#00FF00', '#0000FF'])
    h = .02
    x_min, x_max = X[:, 0].min()-1, X[:, 0].max()+1
    y_min, y_max = X[:, 1].min()-1, X[:, 1].max()+1
    xx, yy = np.meshgrid(np.arange(x_min, x_max, h), np.arange(y_min, y_max, h))
    
    #Z = method.predict(np.c_[xx.ravel(), yy.ravel()])
    Z = Z.reshape(xx.shape)

    plt.figure()
    plt.pcolormesh(xx, yy, Z, cmap=cmap_light)
    plt.scatter(X[:, 0], X[:, 1], c=y, cmap=cmap_bold, edgecolor='k', s=20)
    plt.xlim(xx.min(), xx.max())
    plt.ylim(yy.min(), yy.max())
    #plt.title(title % (costant))
    plt.show()

def calculate_perc(X, y, perc=True):
    sums_true = []
    sums_false = []
    X_set = set(X)
    
    for i in X_set:
        sum_true = 0
        sum_false = 0
        for j, label in zip(X, y):
            if i == j:
                if label is True:
                    sum_true = sum_true + 1
                else:
                    sum_false = sum_false + 1
        sums_true.append(sum_true)
        sums_false.append(sum_false)
    
    if perc is False:
        return sums_true, sums_false
    
    sums_tot = [i + j for i, j in zip(sums_false, sums_true)]
    perc_false = np.divide(sums_false, sums_tot) * 100
    perc_true = np.divide(sums_true, sums_tot) * 100
    
    return perc_true, perc_false

### Explore the Dataset

The dataset has 12330 rows and 18 columns.

There aren't missing values in the dataset.

We can see a part of the dataset to understand the type of the attributes:

In [3]:
dataset = pd.read_csv('online_shoppers_intention.csv')
dataset.head()

result = {} # dictiornary with all the result
best_model = {}

The attributes "Month", "VisitorType", "Weekend" and "Revenue" have  string values and they are changed in numerical values.

The attributes "Administrative", "Informational", "ProductRelated", "OperatingSystems", "Browser", "Region" and "TrafficType" have a finite set of number values. 

The classification is based on the *Revenue* attribute, which has only 2 values, so we have a binary classification.

In [4]:
type_visitors = {
    'New_Visitor': 1,
    'Returning_Visitor': 2,
    'Other': 3
}

months = {
    'Jan': 1,
    'Feb': 2,
    'Mar': 3,
    'May': 5,
    'June': 6,
    'Jul': 7,
    'Aug': 8,
    'Sep': 9,
    'Oct': 10,
    'Nov': 11,
    'Dec': 12
}

bol_value = {
    False: 0,
    True: 1
}
X = dataset.copy()
X['Month'] = X['Month'].replace(months)
X['Revenue'] = X['Revenue'].replace(bol_value)
X['VisitorType'] = X['VisitorType'].replace(type_visitors)
X['Weekend'] = X['Weekend'].replace(bol_value)

X.head()

Administrative  Administrative_Duration  Informational  \
0               0                      0.0              0   
1               0                      0.0              0   
2               0                      0.0              0   
3               0                      0.0              0   
4               0                      0.0              0   

   Informational_Duration  ProductRelated  ProductRelated_Duration  \
0                     0.0               1                 0.000000   
1                     0.0               2                64.000000   
2                     0.0               1                 0.000000   
3                     0.0               2                 2.666667   
4                     0.0              10               627.500000   

   BounceRates  ExitRates  PageValues  SpecialDay  Month  OperatingSystems  \
0         0.20       0.20         0.0         0.0      2                 1   
1         0.00       0.10         0.0         0.0      2                 2   
2         0.20       0.20         0.0         0.0      2                 4   
3         0.05       0.14         0.0         0.0      2                 3   
4         0.02       0.05         0.0         0.0      2                 3   

   Browser  Region  TrafficType  VisitorType  Weekend  Revenue  
0        1       1            1            2        0        0  
1        2       1            2            2        0        0  
2        1       9            3            2        0        0  
3        2       2            4            2        0        0  
4        3       1            4            2        1        0

#### Label Distribution and metric

As we can see in the following bar chart, the label distribution is unbalanced and for this reason I consider the *F-score* as metric.

The number of samples are:
* *True Label*: 1908 samples 
* *False Label*: 10422 samples 


##### F-score 
The *F-score* metric is calculated through the *precision* and *reacall* that are also a metrics.

The *precision* and *recall* metrics are calculated on the *confusion matrix* which is a matrix with predicted labels as columns and the real labels as rows. In this way we have the cells that are *True Positive*, *True Negative*, *False Negative* and *False Positive* for each combination of the labels.

*Confusion matrix*

|                   |Predict Label A                | Predict Label B       |
|---                | ---                           |---                    |
|**True Label A**   |    *True Positive*              |    *False Positive*     |
|**True Label B**   |    *False Negative*             |    *True Negative*      |

From the *confusion matrix* we can calculate the *precision* and *recall* and then *f-score*

$$precision = \frac{True\ Positive}{True\ Positive + False\ Positive}$$


$$recall = \frac{True\ Positive}{True Positive + False\ Negative}$$


$$f\_score = \frac{2 * Recall * Precision}{Recall + Precision}$$



The bar chart below allows to have on the *Y-axis* the number or the percentage of the samples in base on the value assign or less to the *CheckBox*.

In [5]:
# label distribution

def plot_label_distribution(df, perc = False):
    count_false = np.array([1 for i in df['Revenue'] if i is False]).sum(axis=0)
    count_true = np.array([1 for i in df['Revenue'] if i is True]).sum(axis=0)
    colors = ['#475CC5', '#FF6B00']
    yaxis = 'Count'
    x = ['True', 'False']
    y = [count_true, count_false]
    
    if perc is True:
        perc_false = count_false / (count_false + count_true) * 100
        perc_true = count_true / (count_false + count_true) * 100
        yaxis = 'Percentage'
        y = [perc_true, perc_false]

    fig = go.Figure(data=[
        go.Bar(x=x, y=y, marker_color=colors)
    ])
    fig.update_layout(
                        barmode='group',
                        title='Label Distribution',
                        yaxis= dict(
                            title=yaxis,  
                        ),
                        xaxis=dict(
                            title='Revenue'
                        ),
                     )
    iplot(fig)

plot_label_distribution(dataset, False)

We can see in the following tables thanks to *describe* function of *pandas* which showes us:

* *count*: the number of samples
* *std*: the standard deviation for each feature
* *min*: the minimum value of the feature
* *25%*: The first percentile (the lower one)
* *50%*: The second percentile (the median)
* *75%*: The third percentile (the upper one)
* *max*: the maximum value of the feature


In [6]:
dataset.describe()

Administrative  Administrative_Duration  Informational  \
count    12330.000000             12330.000000   12330.000000   
mean         2.315166                80.818611       0.503569   
std          3.321784               176.779107       1.270156   
min          0.000000                 0.000000       0.000000   
25%          0.000000                 0.000000       0.000000   
50%          1.000000                 7.500000       0.000000   
75%          4.000000                93.256250       0.000000   
max         27.000000              3398.750000      24.000000   

       Informational_Duration  ProductRelated  ProductRelated_Duration  \
count            12330.000000    12330.000000             12330.000000   
mean                34.472398       31.731468              1194.746220   
std                140.749294       44.475503              1913.669288   
min                  0.000000        0.000000                 0.000000   
25%                  0.000000        7.000000               184.137500   
50%                  0.000000       18.000000               598.936905   
75%                  0.000000       38.000000              1464.157213   
max               2549.375000      705.000000             63973.522230   

        BounceRates     ExitRates    PageValues    SpecialDay  \
count  12330.000000  12330.000000  12330.000000  12330.000000   
mean       0.022191      0.043073      5.889258      0.061427   
std        0.048488      0.048597     18.568437      0.198917   
min        0.000000      0.000000      0.000000      0.000000   
25%        0.000000      0.014286      0.000000      0.000000   
50%        0.003112      0.025156      0.000000      0.000000   
75%        0.016813      0.050000      0.000000      0.000000   
max        0.200000      0.200000    361.763742      1.000000   

       OperatingSystems       Browser        Region   TrafficType  
count      12330.000000  12330.000000  12330.000000  12330.000000  
mean           2.124006      2.357097      3.147364      4.069586  
std            0.911325      1.717277      2.401591      4.025169  
min            1.000000      1.000000      1.000000      1.000000  
25%            2.000000      2.000000      1.000000      2.000000  
50%            2.000000      2.000000      3.000000      2.000000  
75%            3.000000      2.000000      4.000000      4.000000  
max            8.000000     13.000000      9.000000     20.000000

#### Distribution of the feature

The correlation matrix is calculated on the *Pearson correlation coefficient* which is calculate, for a pair of random variables *X* and *Y*:
$$\rho_{XY} = \frac{\sigma_{XY}}{\sigma_X \sigma_Y}$$

Where $\sigma_X$ and $\sigma_Y$ are the *standard deviations* and the $\sigma_{XY}$ is the covariance that is
$$\sigma_{XY} = E[(X-E[X])(Y-E[Y])]$$

In the matrix we can observe that we have an high correlation between the attributes *ProductRelated, Informational and Administrative* with *ProductRelated_Duration, Informational_Duration and Administrative_Duration*.
The attributes *TrafficType, Browser, OperatingSystem and Region* are also enough correlated. This correlation could be justfy because people of the same region prefer use the same traffic type, browser and OS.

We can see an inverse correlation between *ExitRates and BounceRates* with the attributes *ProductRelated, Informational and Administrative* with the respective duration.

In [7]:
correlation_matrix = dataset.corr()
trace = go.Heatmap(z=correlation_matrix.values.tolist(), x=correlation_matrix.columns, y=correlation_matrix.columns)
data = [trace]
layout = go.Layout(
    title='Correlation matrix'
)
fig_heatmap = go.Figure(data=data, layout=layout)
iplot(fig_heatmap, filename='heatmap')

#### Box Plots

In the box plots below I compared the attributes *VisitorType* and *Month*, for each *Revenue*, with the *PageValues, ExitRates and BounceRates*. 

Remember the definitions of the attributes *PageValues*, *ExitRates* and *BounceRates*:
* *PageValues:*  feature represents the average value for a web page that a user visited before completing an e-commerce transaction.
* *ExitRates:*  is the percentage of people who left your site from that page. Exits may have viewed more than one page in a session. That means they may not have landed on that page, but simply found their way to it through site navigation.
* *BounceRates:* percentage of visitors who enter the site from that page and then leave ('bounce') without triggering any other requests to the analytics server during that session.

ounceRate: percentage of visitors who enter the site from that page and then leave ('bounce') without triggering any other requests to the analytics server during that session.
PageValue:

From the boxplots of the *VisitorType* we can see that there is an high number of *other* customers that surf more on the page of the e-commerce, than a new or returning visitor, before to complete a purchase. The same situation we have for the value of *ExitRates* when there isn't a purchase (*False* label), but we have an high number of regular customer that leave the e-commerce from the page of the purchase.
At the end we can see that low new customers leave the site without triggering any other requests, and this is a good *"signal"* for the approch for new customers.

The boxplot for the *Month* show us that an high number of sales are in December (from the box plot of *PageValues*), that make sense because in December we have Christmas day, but also in May we have an high number of sales.
The worst month for the revenue is Febrary because from the graphs of *ExitRates and BounceRate*.

In [8]:
def dynamic_boxPlot(dataset, feature_x, feature_y):
    fig = px.box(dataset,
            y=feature_y,
            x=feature_x,
            color="Revenue"
            )
    fig.update_layout(
        title = feature_x +" - "+ feature_y,
        boxmode='group',
         yaxis= dict(
            title=feature_y,  
        ),
        xaxis=dict(
            title=feature_x
        ),
    )
    iplot(fig, filename="box-plot")

# menu for boxplot
dynamic_boxPlot(dataset, "VisitorType", "PageValues")
dynamic_boxPlot(dataset, "VisitorType", "ExitRates")
dynamic_boxPlot(dataset, "VisitorType", "BounceRates")

dynamic_boxPlot(dataset, "Month", "PageValues")
dynamic_boxPlot(dataset, "Month", "ExitRates")
dynamic_boxPlot(dataset, "Month", "BounceRates")

#### Pie Chart

In these graphs we can see the sample's distribution of the purchases for the different browsers, traffic types and operating systenms

In [9]:
# menu for dynamic pieChart
def plot_pieChart_menu(dataset, feature, show_labels='All'):
    
    perc_true, perc_false = calculate_perc(dataset[feature], dataset['Revenue'])
    X_set = set(dataset[feature])  
    x_set = [i for i in X_set]
    
    if show_labels == 'All':
        # true pieChart
        fig = go.Figure(data=[
            go.Pie(labels=x_set,
                  values=perc_true)
        ])
        fig.update_layout(
            title= feature +', Revenue: True'
        )
        iplot(fig, filename="pieChart-True")

        #false pieChart
        fig = go.Figure(data=[
            go.Pie(labels=x_set,
                  values=perc_false)
        ])
        
        fig.update_layout(
            title= feature + ', Revenue: False'
        )
        iplot(fig, filename="pieChart-False")
        
    elif show_labels == 'True':
        # true pieChart
        fig = go.Figure(data=[
            go.Pie(labels=x_set,
                  values=perc_true)
        ])
        fig.update_layout(
            title= feature +', Revenue: True'
        )
        iplot(fig, filename="pieChart-True")
        
    elif show_labels == 'False':
        fig = go.Figure(data=[
            go.Pie(labels=x_set,
                  values=perc_false)
        ])
        fig.update_layout(
            title= feature + ', Revenue: False'
        )
        iplot(fig, filename="pieChart-False")

plot_pieChart_menu(dataset, 'Browser', 'True')
plot_pieChart_menu(dataset, 'OperatingSystems', 'True')
plot_pieChart_menu(dataset, 'TrafficType', 'True')


#### Bar Chart
In the following bar charts we can see the distribution of the labels for the different regions, the weekend and also for the visitor types.

From the first graph we can say that the highest number of customers are from the region 1.

The high number of sales are done not in the weekend, we can image a situation such as in Italy that on the Saturday and Sunday there aren't delivery services.

The the high number of purchases are done by returning visitors, we can interpretate for the client that had have a good service and return on the e-commerce.

In [10]:
# menu for dynamic barChart
def dynamic_barChart(dataset, feature, perc):
    sums_true = []
    sums_false = []
    
    X_set = set(dataset[feature])  
    x_set = [i for i in X_set]
    y = dataset['Revenue']
    
    if perc is False:
        title = "Number of samples for each revenue of " + feature
        yaxis = "Number of samples"
    else:
        title = "Percentage of samples for each revenue of " + feature
        yaxis = "Percantage of samples %"
        
    perc_true, perc_false = calculate_perc(dataset[feature], y, perc)
    fig = go.Figure(data=[
        go.Bar(name='True', x=x_set, y=perc_true),
        go.Bar(name='False', x=x_set, y=perc_false)
    ])
    fig.update_layout(
                        barmode='group',
                        title=title,
                        yaxis= dict(
                            title=yaxis,  
                        ),
                        xaxis=dict(
                            title=feature
                        ),
                     )
    iplot(fig, filename='barChart')

dynamic_barChart(dataset, 'Region', False)
dynamic_barChart(dataset, 'Weekend', False)
dynamic_barChart(dataset, 'VisitorType', False)

### Preparing the dataset 

Tha dataset is divide to training and test set in the percentage of 80\% and 20\% respectively.

I normalize the data throught the *StandardScaler* method of *sklearn*. This method calculated the standard score of a sample *X*:
$$ Z = \frac{X - \mu}{\sigma} $$ 

The method *StandardScaler* fits the training set and transforms the test set on the $\mu$ and $\sigma$ of the training set.
In this way our distribution has the mean value 0 and the standard deviation of 1.

To avoid the overfitting I use the *k-fold cross-validation* with $K = 10$. This method divides the training set into *K* subsets, one of this subset is used as the validation set and the other *K-1* subsets are put together to form a training set. In this case our training set is 9864 samples and the method is trained on 8878 samples and validate on 986 samples.

In [11]:
y = X['Revenue'].copy()
X = X.drop(['Revenue'], axis=1)

#### Principal Component Analysis

The PCA is a method that combines highly correlated variables together to form a smaller number of an artificial set of variables which is called "principal components" that account for most variance in the data.

The steps for the PCA starting from a dataset of *n x m* to a new dataset of *k* variables :
1. normalize the dataset **X** *(n x m)*.
2. calculate the *covariance* matrix **V**.
3. calculate the *eigen values and vectors* of the *covariance* matrix and sort them in descending order.
4. build the **W** matrix putting the top *k* eigenvectors into columns of **W** *(n x k)*.
5. calculate $X_T = X W$.

The graph below showes us the number of components I used in base on the percentage of the variance. This graph is the result from the PCA's attribute *explained_variance_*  that returns the amount for each component. Creating an agglomerative list it's possible to understand the single and the cumulative variance.

It's possible to see that with *n_components = 10* we have about 80\% of the total variance.

In [12]:
scaler = StandardScaler()
X_scaler = scaler.fit_transform(X)
pca = PCA()
df_X_pca = pca.fit_transform(X_scaler)

tot = sum(pca.explained_variance_)
var_exp = [(i/tot) * 100 for i in sorted(pca.explained_variance_, reverse=True)] # amount of variance for each components
cum_var_exp = np.cumsum(var_exp) # cumulative sum

trace_cum_var_exp = go.Bar(
    x=list(range(1, len(cum_var_exp) + 1)), 
    y=var_exp,
    name="individual explained variance",
)

trace_ind_var_exp = go.Scatter(
    x=list(range(1, len(cum_var_exp) + 1)),
    y=cum_var_exp,
    mode='lines+markers',
    name="cumulative explained variance",
    line=dict(
        shape='hv',
    ))
data = [trace_cum_var_exp, trace_ind_var_exp]
layout = go.Layout(
    title='Variance and PCA',
    autosize=True,
    yaxis=dict(
        title='Percentage of variance',
    ),
    xaxis=dict(
        title="n_components PCA",
        dtick=1,
    ),
    legend=dict(
        x=0,
        y=1,
    ),
)
fig = go.Figure(data=data, layout=layout)
iplot(fig, filename='basic-bar')

# n_components = 10
pca = PCA(n_components=10)
# X_pca = pca.fit_transform(X)

X_train, X_test, y_train, y_test = train_test_split(X, y, train_size=0.8, test_size=0.2, random_state=1)

X_train = pca.fit_transform(X_train)
X_test = pca.transform(X_test)

print('X_train: ', X_train.shape)
print('y_train: ', y_train.shape)
print('X_test:', X_test.shape)
print('y_test: ', y_test.shape)

sm = SMOTE(random_state=50)
X_train, y_train = sm.fit_sample(X_train, y_train)
#X_test, y_test = sm.fit_sample(X_test, y_test)

X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

X_train:  (9864, 10)
y_train:  (9864,)
X_test: (2466, 10)
y_test:  (2466,)


In [13]:
from tabulate import tabulate

def calculate_gridsearchCV(method, parameters, X_test, y_test, num_jobs=1, show_score_train=False, n_top_scores=5):
    kfold = KFold(n_splits=10)
    clf_model = GridSearchCV(method, parameters, scoring='f1', cv=kfold, n_jobs=num_jobs, return_train_score=show_score_train).fit(X_train, y_train)
    y_predict = clf_model.predict(X_test)
    
    """
    cv_results_=
    {
        'param_kernel': masked_array(data = ['poly', 'poly', 'rbf', 'rbf'],
                                     mask = [False False False False]...)
        'param_gamma': masked_array(data = [-- -- 0.1 0.2],
                                    mask = [ True  True False False]...),
        'param_degree': masked_array(data = [2.0 3.0 -- --],
                                     mask = [False False  True  True]...),
        'split0_test_score'  : [0.80, 0.70, 0.80, 0.93],
        'split1_test_score'  : [0.82, 0.50, 0.70, 0.78],
        'mean_test_score'    : [0.81, 0.60, 0.75, 0.85],
        'std_test_score'     : [0.01, 0.10, 0.05, 0.08],
        'rank_test_score'    : [2, 4, 3, 1],
        'split0_train_score' : [0.80, 0.92, 0.70, 0.93],
        'split1_train_score' : [0.82, 0.55, 0.70, 0.87],
        'mean_train_score'   : [0.81, 0.74, 0.70, 0.90],
        'std_train_score'    : [0.01, 0.19, 0.00, 0.03],
        'mean_fit_time'      : [0.73, 0.63, 0.43, 0.49],
        'std_fit_time'       : [0.01, 0.02, 0.01, 0.01],
        'mean_score_time'    : [0.01, 0.06, 0.04, 0.04],
        'std_score_time'     : [0.00, 0.00, 0.00, 0.01],
        'params'             : [{'kernel': 'poly', 'degree': 2}, ...],
        }
    """

    print("Top %d mean of f1-scores on validation set" % n_top_scores)
    top_scores_indexes = np.argsort(clf_model.cv_results_['mean_test_score'], axis=-1)[:n_top_scores]
    top_scores_mean = clf_model.cv_results_['mean_test_score'][top_scores_indexes]
    top_parameters = np.array(clf_model.cv_results_['params'])[top_scores_indexes]
    
    elements = list()
    for index, score, parameters in zip(range(0, n_top_scores),top_scores_mean, top_parameters):
        elements.append([score, parameters])
    
    print(tabulate(elements, headers=['Mean f1-score', 'Parameters']))
    
    print('Best score on validation set: ', clf_model.best_score_)
    print('Classification report on test set:')
    print(classification_report(y_test, y_predict))
    print('F1-score on test set: ', f1_score(y_test, y_predict))
    print('Best parameters: ', clf_model.best_params_)
    
    return clf_model.best_estimator_

#### K-Neighbors Classifier

The first method that I approch is the *K-Neighbors Classifier*. The main parameter is the value of *K* which defines the number of unlabel element's *neighbors* with labels and the major number of element with the same labels determinate the label of our unknown point.

I have used the *GridSearchCV* to find the best parameters of *K-Neighbors Classifier*. The candidates of the parameters are:
* *K* = number of neighbors, values 3, 5, 7, 9, 11, 13
* *p* = the metric to use for the distance: 1 (Manhattan distance) or 2 (Euclidean distance)
    * *Manhattan distance*: the Manhattan distance between two points ***p***=$(p1, p2 ... p_N)$ and ***q***=$(q_1, q_2, ... q_N)$ is:
        $$\sum_{i=1}^{N}|q_i  - p_i|$$
    * *Euclidean distance*: the Euclidean distance between two points ***p***=$(p1, p2 ... p_N)$ and ***q***=$(q_1, q_2, ... q_N)$ is:
        $$\sqrt{\sum_{i=1}^{N}(q_i  - p_i)^2} $$ 
        
* *weights*: determinates the importance of the point,
    * *uniform*: the points in each neighborhood are weighted equally.
    * *distance*: the weight of the point is the inverse of the distance, in this case closer neighbors are more influence than neighbors which are distant.

In [14]:
knn = KNeighborsClassifier()
parameters = {
    'n_neighbors': [3, 5, 7, 9, 11, 13],
    'p': [1, 2],     # for metrics Euclidean Distance, Minkowski
    'weights': ['uniform', 'distance']
}
best_model['KNN'] = calculate_gridsearchCV(knn, parameters, X_test, y_test, num_jobs=4, show_score_train=True)

Top 5 mean of f1-scores on validation set
  Mean f1-score  Parameters
---------------  -------------------------------------------------
       0.720512  {'n_neighbors': 13, 'p': 2, 'weights': 'uniform'}
       0.725372  {'n_neighbors': 11, 'p': 2, 'weights': 'uniform'}
       0.730554  {'n_neighbors': 9, 'p': 2, 'weights': 'uniform'}
       0.73994   {'n_neighbors': 7, 'p': 2, 'weights': 'uniform'}
       0.747913  {'n_neighbors': 13, 'p': 1, 'weights': 'uniform'}
Best score on validation set:  0.806921224507993
Classification report on test set:
              precision    recall  f1-score   support

           0       0.77      0.87      0.82      2115
           1       0.85      0.75      0.79      2115

    accuracy                           0.81      4230
   macro avg       0.81      0.81      0.80      4230
weighted avg       0.81      0.81      0.80      4230

F1-score on test set:  0.7931555108203322
Best parameters:  {'n_neighbors': 3, 'p': 1, 'weights': 'distance'}


#### Support Vector Machine

The aim of the *linear Support Vector Machine (SVM)* algorithm is to find a hyperplane in an N-dimensiona space (N is the numer of features) that distinctly classifies the data points with the maximum distance betweens both classes. 

In case the dataset isn't linearly separable, we can map the samples *X* into a feature space of more dimensions 
$$ X \rightarrow \phi(X)$$

which the samples of the classes can be lienarly saprated. 

As the vectors *$X_i$* appear only in inner products in bothe the decision function and the learning law, the mapping function $\phi(X)$ doesn't need to be explicitly specified. Instead we define a so-called kernel function:

I have used the following kernels:
* *Linear*: $K(X_1,X_2) = X_1 \cdot X_2$ 
* *Radial Basis Function (rbf)* = $K(X_1, X_2 ) = e^{-\gamma(||X_1 - X_2||^2)}$

The hyperparameters candidate for the *GridSearchCV* are the following:

* *kernel*: the kernel used, 'rbf' or 'linear'
* *C*: trades off correct classification of training examples against maimization of the decision funcion's margin. The values candidate are 0.01, 1, 10, 100 and 1e3.
* *gamma*: defines how far the influence of a single training example reaches, with low values meaning 'far' and high values meaning 'close'. The values candidate are 1e-3, 0.01, 1e-6 and 1e-9.


In [15]:
svm_linear = SVC(kernel='linear', probability=True)
parameters ={
    'C': [10]
}
# best_model['SVM_linear'] = calculate_gridsearchCV(svm_linear, parameters, X_test, y_test, num_jobs=2)


In [16]:
svc_model = SVC(probability=True)
parameters = {
    'kernel': ['rbf'],
    'C': [0.01, 1, 10, 100, 1e3, 1e4],
    'gamma': [1e-3, 0.01, 1e-6, 1e-9],
}

best_model['SVM_rbf'] = calculate_gridsearchCV(svc_model, parameters, X_test, y_test, num_jobs=2, show_score_train=True)

Top 5 mean of f1-scores on validation set
  Mean f1-score  Parameters
---------------  ----------------------------------------------
       0.171199  {'C': 10, 'gamma': 1e-09, 'kernel': 'rbf'}
       0.171199  {'C': 1000.0, 'gamma': 1e-09, 'kernel': 'rbf'}
       0.171199  {'C': 0.01, 'gamma': 1e-06, 'kernel': 'rbf'}
       0.171199  {'C': 0.01, 'gamma': 1e-09, 'kernel': 'rbf'}
       0.171199  {'C': 100, 'gamma': 1e-09, 'kernel': 'rbf'}
Best score on validation set:  0.7814141083385656
Classification report on test set:
              precision    recall  f1-score   support

           0       0.84      0.90      0.87      2115
           1       0.89      0.83      0.86      2115

    accuracy                           0.86      4230
   macro avg       0.86      0.86      0.86      4230
weighted avg       0.86      0.86      0.86      4230

F1-score on test set:  0.8577734183423247
Best parameters:  {'C': 10000.0, 'gamma': 0.01, 'kernel': 'rbf'}


#### Decision Tree

A decision tree is drawn upside down with its root at the top and the leaf at the bottom. Internal nodes of the tree represent the conditio, based on which the tree splits into edges. The end of the edge (the leaf) is the label.

The decision tree is built with a greedy algorithm given that the minimal theoretical function exists but it's NP-hard for the number of partitions which has a factorial growth.

The parameters for the GridSearch are:
* *criterion*: fuction to measure the quality of split *gini* or *entropy*
    * *Gini index* for *J* classes 
        $$ Gini = 1 - \sum_{j=0}^J p_j^2$$
        where $\hat{p}_{j}$ represents the portion of an element to be with that label.
    * *Entropy* is calculated:
        $$ Entropy = - \sum_{j=0}^J p_j \log_2 p_j$$
* *splitter*: the strategy used to choose the split at aech node, *best* to choose the best split and *random* to choose the best random split.
* *max_depth*: the maximum depth of the tree between 25, 50, 75 and 100.
* *min_samples_split*: the minimum number of samples required to split an internal node, 3, 6, 10 or 12.

In [17]:
decisionTree = DecisionTreeClassifier()
parameters = {
    'criterion': ['gini', 'entropy'],
    'splitter': ['best', 'random'],
    'max_depth': [25, 50, 75, 100],
    'min_samples_split': [3, 6, 10, 12]
}
best_model['DecisionTreeClassifier'] = calculate_gridsearchCV(decisionTree, parameters, X_test, y_test, num_jobs=4)

Top 5 mean of f1-scores on validation set
  Mean f1-score  Parameters
---------------  ----------------------------------------------------------------------------------------
       0.7532    {'criterion': 'gini', 'max_depth': 100, 'min_samples_split': 12, 'splitter': 'random'}
       0.753572  {'criterion': 'gini', 'max_depth': 100, 'min_samples_split': 10, 'splitter': 'random'}
       0.754261  {'criterion': 'entropy', 'max_depth': 25, 'min_samples_split': 6, 'splitter': 'random'}
       0.755963  {'criterion': 'gini', 'max_depth': 75, 'min_samples_split': 6, 'splitter': 'random'}
       0.756064  {'criterion': 'entropy', 'max_depth': 25, 'min_samples_split': 12, 'splitter': 'random'}
Best score on validation set:  0.7809116955834782
Classification report on test set:
              precision    recall  f1-score   support

           0       0.79      0.88      0.83      2115
           1       0.86      0.76      0.81      2115

    accuracy                           0.82      4230


#### Random Forest Classifier

The *Random Forest Classifier* consists in a set of individual decision trees that operate as an ensamble. Each individual tree in the random forest splits out a class prediction and the class with the most votes becomes out model's prediction. This independence for the classification of the label allow to be a very strong method against outlines.

The hyperparameters candidate for the *GridSearchCV* are:
* *max_depth*: the maximum depth of the tree between 50, 75 or 100.
* *criterion*: the function to measure the quality of a split, *gini* or *entropy*.

* *n_estimators*: number of trees, candidates are [100, 300, 500].


In [18]:
rfc_model = RandomForestClassifier()
parameters = {
    "max_depth": [50, 75, 100],
    "criterion": ['entropy', 'gini'],
    "n_estimators": [100, 300, 500]
}

best_model['RandomForestClassifier'] = calculate_gridsearchCV(rfc_model, parameters, X_test, y_test, num_jobs=4)

Top 5 mean of f1-scores on validation set
  Mean f1-score  Parameters
---------------  ---------------------------------------------------------------
       0.836666  {'criterion': 'entropy', 'max_depth': 50, 'n_estimators': 500}
       0.838081  {'criterion': 'entropy', 'max_depth': 75, 'n_estimators': 300}
       0.838373  {'criterion': 'entropy', 'max_depth': 50, 'n_estimators': 300}
       0.838428  {'criterion': 'entropy', 'max_depth': 100, 'n_estimators': 300}
       0.838563  {'criterion': 'entropy', 'max_depth': 75, 'n_estimators': 500}
Best score on validation set:  0.8430143778884622
Classification report on test set:
              precision    recall  f1-score   support

           0       0.86      0.90      0.88      2115
           1       0.89      0.85      0.87      2115

    accuracy                           0.88      4230
   macro avg       0.88      0.88      0.88      4230
weighted avg       0.88      0.88      0.88      4230

F1-score on test set:  0.87282398452

#### ROC CURVE

The ROC curve (receiver operating characteristic curve) is a graph that showes the performance of a classifier at all classification thresholds. The graph is plotted through 2 variable:
* True positive rate: calculate as the recall metric, and it's defined as:
$$ TPR = \frac{True\ Positive}{True\ Positive + False\ Negative}$$
* False positive rate: defined as:
$$ FPR = \frac{False\ Positive}{False\ Positive + True\ Negative}$$

The plot is based on *TPR vs FPR* at the different classification thresholds.

As metric for the compare it's used the *AUC (Area Under the ROC Curve)*. It's a measure that aggregates measure of performance across all possible classfication thresholds, so it tells how much model is capable of distringuishing between classes. Higher the AUC is and better the model classifies 0s as 0as and 1s and 1s. 



In [19]:
# Plotting ROC curve

def plot_roc_curve(methods, name_methods, X_test, y_test):
    fpr = dict()
    tpr =dict()
    roc_auc = dict()
    fig = go.Figure()
    y_test_roc = np.array([([0, 1] if y else [1, 0]) for y in y_test])
    for method, name in zip(methods, name_methods):
        y_score = method.predict_proba(X_test)
        fpr["micro"], tpr["micro"], _ = roc_curve(y_test_roc.ravel(), y_score.ravel())
        roc_auc["micro"] = auc(fpr["micro"], tpr["micro"])
        
        fig.add_trace(
            go.Scatter(x=fpr['micro'], y=tpr['micro'], 
                       mode='lines', name=name + " (auc = %0.2f) "% roc_auc["micro"] )
        )
        
    fig.add_trace(
        go.Scatter(x=[0,1], y=[0,1], line=dict(
                              dash='dash'), showlegend=False)
    )
    
    fig.update_layout(title='ROC curve', xaxis_title='FPR', yaxis_title='TPR') 
    fig.show()


plot_roc_curve(best_model.values(), best_model.keys(), X_test, y_test)

### Clustering

In this section, I wanted to focus on the unsupervised learning algorithms, which allows us to identify similar cluster of data points within your data.

The aim is to partition the dataset in base of the kind of customers. The clusters are 3 as the attribute *VisitorType*:
* *New Visitor*
* *Returning Visitor*
* *Other*

The algorithms that I used are:

* KMeans
* Hierarchical

I started from initial dataset, I replaced the non digit attributes, removed the attribute *VisitorType* and normalized the dataset.

The metric used to evaluate the working of the algorithm is the *Silhouette*.

The *silhouette* for the data point $i \in C_i$, 
$$ s(i) = \frac{b(i) - a(i)}{max\{a(i), b(i)\}}$$
where *a(i)* is the mean distance between *i* and all other data points in the same cluser
$$ a(i) = \frac{1}{|C_i - 1|} \sum_{j \in C_i, i\neq j} d(i,j)$$
while *b(i)* is the smallest mean distance of *i* to all points in any other cluster, of *i* is not a memeber.
$$ b(i) = \min_{k \neq i} \frac{1}{|C_k|} \sum_{j \in C_k} d(i, j)$$




In [20]:
X = dataset.copy()
X['Month'] = X['Month'].replace(months)
X['Revenue'] = X['Revenue'].replace(bol_value)
X['VisitorType'] = X['VisitorType'].replace(type_visitors)
X['Weekend'] = X['Weekend'].replace(bol_value)

y = X['VisitorType'].copy()
X = X.drop(['VisitorType'], axis=1)

X_train, X_test, y_train, y_test = train_test_split(X, y, train_size=0.8, test_size=0.2, random_state=1)

X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

#### K-MEANS 

This algorithm is based on the idea that we define the number of clusters *k* but define also the number of *centroids*. A centroid is the imaginary or real location representing the center of the cluster.

The algorithm works in the following steps:

1. At the begging of the algorithm the centroids are chosen randomly
2. Each centroids calculate the data point closer to identify the cluster's points
3. In each cluster is calculated the mean distance which becomes the new centroid of the cluster. 
4. The algorithm restarts from the step 2 until it reaches the max number of iteration.

The parameters that I set are:
* *n_cluster = 3*
* *max_iteration = 2000*

In [21]:
kmeans = KMeans(n_clusters=3, max_iter=2000).fit(X_train)
y_predict = kmeans.predict(X_test)
print(silhouette_score(X_test, y_predict))

0.2614833302888594


#### Hierarchical

This method doesn't require a choice for the number of cluster, but we have a *dendogram*, a tree-graph, which allow us to view at once the clustering obteined for each possible number of clusters, from 1 to *n*.

The approch that I used is the *agglomerative* (or *bottom-up*) approach which finds the 2 "*closest*" cluster, merge them and repeat till the end of the points are in one unique cluster.

The distance between two clusters can be similiraty, dissimilary or distance, in my case I choice the distance based on correlation.

The distance from the point is different in base on the type of linkage selected:
* *Complete linkage clustering or maximum:* 
    $$ \max \{ d(a, b): a \in A, b \in B \}$$
* *Single linkage clustering or minimum:*
    $$ \min \{ d(a, b): a \in A, b \in B\}$$
* *Centroid linkage clustering:*
    $$ ||c_s - c_t ||$$
     where $c_s$ and $c_t$ are the centroids of clusters *s* and *t*.
* *Average linkage:*
    $$ \frac{1}{|A||B|} \sum_{a \in A} \sum_{b \in B} d(a, b)$$

In the following graphs are represented the dendogram with the the *average, complete and single linkage* and we can see that the hierarchial is different as the "position" of the red line, which marks when we have the 3 clusters.

Which is the best? find a solution

In [22]:
X = dataset.copy()
X['Month'] = X['Month'].replace(months)
X['Revenue'] = X['Revenue'].replace(bol_value)
X['VisitorType'] = X['VisitorType'].replace(type_visitors)
X['Weekend'] = X['Weekend'].replace(bol_value)

X = X.drop(['VisitorType'], axis=1)
names = X.columns
inverse_corr = 1 - np.abs(X.corr())

X = np.random.rand(17, 1000) # 17 features of 1000 samples

# average-linkage
fig = ff.create_dendrogram(inverse_corr, labels=names, linkagefun=lambda x: hierarchy.linkage(x, 'average') )

fig.add_trace(go.Scatter(y=[1.48, 1.48],x=[0, 170] , mode="lines"))

fig['layout'].update(dict(
    title="Hierarchical clustering on the average-linkage",
    xaxis=dict(
        title='Features',
    ),
    yaxis=dict(
        title='Distance',
        automargin=True,
    ),
))
iplot(fig, filename='dendrogram_corr_clustering')

clustering = AgglomerativeClustering(n_clusters=3, affinity='precomputed', linkage='average').fit(inverse_corr)
print('Silhouette score: ', silhouette_score(X, clustering.labels_))

#complete-linkage
fig = ff.create_dendrogram(inverse_corr, labels=names, linkagefun=lambda x: hierarchy.linkage(x, 'complete') )
fig['layout'].update(dict(
    title="Hierarchical clustering on the complete-linkage",
    xaxis=dict(
        title='Features',
    ),
    yaxis=dict(
        title='Distance',
        automargin=True,
    ),
))
fig.add_trace(go.Scatter(y=[1.6, 1.6],x=[0, 170] , mode="lines"))
iplot(fig, filename='dendrogram_corr_clustering')

clustering = AgglomerativeClustering(n_clusters=3, affinity='precomputed', linkage='complete').fit(inverse_corr);
print('Silhouette score: ', silhouette_score(X, clustering.labels_))


# single-linkage
fig = ff.create_dendrogram(inverse_corr, labels=names, linkagefun=lambda x: hierarchy.linkage(x, 'single') )
fig['layout'].update(dict(
    title="Hierarchical clustering on the single-linkage",
    xaxis=dict(
        title='Features',
    ),
    yaxis=dict(
        title='Distance',
        automargin=True,
    ),
))
fig.add_trace(go.Scatter(y=[1.383, 1.383], x=[0, 170] , mode="lines"))
iplot(fig, filename='dendrogram_corr_clustering')

clustering = AgglomerativeClustering(n_clusters=3, affinity='precomputed', linkage='single').fit(inverse_corr);
print('Silhouette score: ', silhouette_score(X, clustering.labels_))


Silhouette score:  0.00033547884668258234


Silhouette score:  0.00033547884668258234


Silhouette score:  0.00033547884668258234
